# Imports

Import necessary modules

In [ ]:
%reload_ext autoreload
%autoreload 1
#%aimport libinstall
from general import *
from preprocessing import *
from segmentation import *
from feature_extraction import *
from activity_fetcher import *
from classifier import *
from combiner import *
from evalutation import *
from metric import *



In [ ]:
def makeTrainTest(sensor_events,activity_events):
    dataset_split=min(activity_events.StartTime)+((max(activity_events.EndTime)-min(activity_events.StartTime))*4/5)
    dataset_split=pd.to_datetime(dataset_split.date())#day
    Train=Data('train')
    Test=Data('test')
    Train.s_events=sensor_events[sensor_events.time<dataset_split]
    Train.a_events=activity_events[activity_events.EndTime<dataset_split]

    Test.s_events=sensor_events[sensor_events.time>=dataset_split]
    Test.a_events=activity_events[activity_events.EndTime>=dataset_split]

    return [Train],[Test]

def makeFoldTrainTest(sensor_events,activity_events,fold):
    sdate=sensor_events.time.apply(lambda x:x.date())
    adate=activity_events.StartTime.apply(lambda x:x.date())
    days=adate.unique()
    kf = KFold(n_splits=fold)
    kf.get_n_splits(days)

    for j,(train_index, test_index) in enumerate(kf.split(days)):
        Train0=Data('train_fold_'+str(j))
        Train0.s_events=sensor_events.loc[sdate.isin(days[train_index])]
        Train0.a_events=activity_events.loc[adate.isin(days[train_index])]
        Test0=Data('test_fold_'+str(j))
        Test0.s_events=sensor_events.loc[sdate.isin(days[test_index])]
        Test0.a_events=activity_events.loc[adate.isin(days[test_index])]
        yield Train0,Test0

# Model Visualization

In [ ]:
def plot_confusion_matrix(matrix,labels,figsize=[15,15]):
  import seaborn as sn
  import pandas as pd
  import matplotlib.pyplot as plt

  df_cm = pd.DataFrame(np.array(matrix).round(1), index = labels,
                  columns = labels)
  #from confusion_matrix_pretty_print import pretty_plot_confusion_matrix
  
  #sn.heatmap(df_cm, annot=True)
  cmap = 'PuRd'
  
  pretty_plot_confusion_matrix(df_cm, cmap=cmap,figsize=figsize)

# Real Accuracy

In [ ]:
def plotAct(acts):
  firstacts=acts.iloc[0];
  lastact=acts.iloc[-1];
  lastactinDay=acts.loc[acts['StartTime']<firstacts['StartTime']+pd.Timedelta('10h')].iloc[-1];
  for a in activities:
    acts=acts.append({'Activity':activities_map_inverse[a],'StartTime':firstacts['StartTime'],'EndTime':firstacts['StartTime']},ignore_index=True)
    
  acts=acts.sort_values(by='Activity')
  
  df2=acts.apply(lambda x:dict(Task=activities_map[x.Activity],Color=0, Start=x.StartTime, Finish=x.EndTime), axis=1).tolist()
  #configure_plotly_browser_state()
  init_notebook_mode(connected=False)
  #fig=ff.create_gantt(df2, index_col='Color', group_tasks=True)
  import plotly.figure_factory as ff

  fig=ff.create_gantt(df2, group_tasks=True)
  fig['layout'].update(margin=dict(l=150))
  fig['layout'].update(xaxis=dict(
        range=[firstacts['StartTime'], lastactinDay['EndTime']],
        rangeselector=dict(
            buttons=list([
                dict(count=4,
                     label='4h',
                     step='hour',
                     stepmode='backward'),
                dict(count=6,
                     label='6h',
                     step='hour',
                     stepmode='backward'),
                dict(count=8,
                     label='8h',
                     step='hour',
                     stepmode='backward'),
                dict(count=10,
                     label='10h',
                     step='hour',
                     stepmode='backward'),
                dict(count=12,
                     label='12h',
                     step='hour',
                     stepmode='backward'),
                dict(count=1,
                     label='1d',
                     step='day',
                     stepmode='backward'),
                dict(count=5,
                     label='5d',
                     step='day',
                     stepmode='backward'),
                
                dict(step='all')
            ])
        ),rangeslider=dict(
            visible = True,
            range=[firstacts['StartTime'], lastact['EndTime']],
        )))
  iplot( fig)
#plotAct(activity_events)


In [ ]:
#acts=testact
#firstacts=acts.iloc[0];
#lasttime=firstacts['StartTime']+pd.Timedelta('10h');
#acts.loc[acts['StartTime']<lasttime].iloc[-1]

In [ ]:
def test(model,test):
    testact=[]
    testactp=[]
    testact=Test.a_events
    #for i in range(0,len(Test.set_window[0])):
        #testact.append({'Activity':test_label[i],'StartTime':test_set_window[i]['start'],'EndTime':test_set_window[i]['end']})


    for a in activities_map:
      pacts=model[a].predict_classes(Test.set[a])
      for i in range(0,len(Test.set_window[a])):
        if(pacts[i]!=0):
          testactp.append({'Activity':a,'StartTime':Test.set_window[a][i]['start'],'EndTime':Test.set_window[a][i]['end']})
  
    #plotAct(testact[1:1000])
    plotAct(pd.DataFrame(testact))
    plotAct(pd.DataFrame(testactp))


In [ ]:
def merge_split_overlap_IntervalTree(p_acts,r_acts):
    tree=IntervalTree()

    for act in p_acts:
        start=act['StartTime'].value;
        end=act['EndTime'].value;
        if(start==end):
            start=start-1
        #tree[start:end]={'P':{'Activitiy':act.Activity,'Type':'P','Data':act}]
        d=Data('P-act')
        d.P=act
        d.R=None
        tree[start:end]=d #{'P':act,'PActivitiy':act.Activity}
        
    for act in r_acts:
        start=act['StartTime'].value;
        end=act['EndTime'].value;
        if(start==end):
            start=start-1
        #tree[start:end]=[{'Activitiy':act.Activity,'Type':'R','Data':act}]
        d=Data('P-act')
        d.P=None
        d.R=act
        tree[start:end]=d #{'R':act,'RActivitiy':act.Activity}

    tree.split_overlaps()
    def data_reducer(x,y):
        res=x
        if not(y.P is None):
            if (res.P is None) or y.P['EndTime']<res.P['EndTime']:
                res.P=y.P
        if not(y.R is None):
            if (res.R is None) or y.R['EndTime']<res.R['EndTime']:
                res.R=y.R
        return res
    
    tree.merge_equals(data_reducer=data_reducer)
            
    return tree

In [ ]:


def myaccuracy(predicted0,real0):
  begin=real0.StartTime.min()
  end=real0.EndTime.max()
  predicted=[p for i,p in predicted0.iterrows()]
  real=[p for i,p in real0.iterrows()]

#   predicted.append({'StartTime':begin,'EndTime':end,'Activity':0})
#   real.append({'StartTime':begin,'EndTime':end,'Activity':0})
  events=merge_split_overlap_IntervalTree(predicted,real)
  #predictedtree=makeIntervalTree(labels)

  cm=np.zeros((len(activities),len(activities)))
  
  for eobj in events:
      e=eobj.data
      pact=e.P.Activity if not(e.P is None) else 0
      ract=e.R.Activity if not(e.R is None) else 0
      cm[pact][ract]+=max((eobj.end-eobj.begin)/pd.to_timedelta('60s').value,0.01);
        
  #for p in predicted:
  #  for q in realtree[p['StartTime'].value:p['EndTime'].value]:
  #      timeconfusion_matrix[p['Activity']][q.data['Activity']]+=findOverlap(p,q.data);
        
  return cm

#test_a_events_arr=[x for i,x in test_a_events.iterrows() ]
#matrix=myaccuracy(test_a_events_arr,testactp)
#pd.DataFrame(matrix)
#plot_confusion_matrix(matrix,activities)
#ev=prepareEval(runs)
# print(ev[0]['cm'])
# np.set_printoptions(precision=0)
# np.set_printoptions(suppress=True)

# print(np.array(ev[0]['mycm']))

In [ ]:
def myaccuracy2(predicted0,real0):
  predicted=[p for i,p in predicted0.iterrows()]
  real=[p for i,p in real0.iterrows()]
  realtree=makeIntervalTree(real)
  #predictedtree=makeIntervalTree(predicted)
  predictedtree=makeNonOverlapIntervalTree(predicted)
  #predictedtree=makeIntervalTree(labels)

  timeconfusion_matrix=np.zeros((len(activities),len(activities)))
  
  for p in real:
    for q in predictedtree[p['StartTime'].value:p['EndTime'].value]:
      timeconfusion_matrix[p['Activity']][q.data['Activity']]+=findOverlap(p,q.data);
        
  #for p in predicted:
  #  for q in realtree[p['StartTime'].value:p['EndTime'].value]:
  #      timeconfusion_matrix[p['Activity']][q.data['Activity']]+=findOverlap(p,q.data);
        
  return timeconfusion_matrix

#test_a_events_arr=[x for i,x in test_a_events.iterrows() ]
#matrix=myaccuracy(test_a_events_arr,testactp)
#pd.DataFrame(matrix)
#plot_confusion_matrix(matrix,activities)


## event_confusion_matrix

In [ ]:
def event_confusion_matrix(r_activities,p_activities,labels):
    cm=np.zeros((len(labels),len(labels)))
    # begin=real0.StartTime.min()
    # end=real0.EndTime.max()
    predicted=[p for i,p in p_activities.iterrows()]
    real=[p for i,p in r_activities.iterrows()]

    #   predicted.append({'StartTime':begin,'EndTime':end,'Activity':0})
    #   real.append({'StartTime':begin,'EndTime':end,'Activity':0})
    events=merge_split_overlap_IntervalTree(predicted,real)
    #predictedtree=makeIntervalTree(labels)

    cm=np.zeros((len(activities),len(activities)))
    
    for eobj in events:
        e=eobj.data
        pact=e.P.Activity if not(e.P is None) else 0
        ract=e.R.Activity if not(e.R is None) else 0
        cm[ract][pact]+=max((eobj.end-eobj.begin)/pd.to_timedelta('60s').value,0.01);
            
    #for p in predicted:
    #  for q in realtree[p['StartTime'].value:p['EndTime'].value]:
    #      timeconfusion_matrix[p['Activity']][q.data['Activity']]+=findOverlap(p,q.data);
            
    return cm



##convertAndMergeToEvent

In [ ]:
def convertAndMergeToEvent_old(set_window,predictedclasses):
    events=[]
    for i in range(0,len(set_window)):
        start=set_window[i]['start'];
        end=set_window[i]['end'];
        pclass=predictedclasses[i]
        if(len(events)>0):
            last=events[len(events)-1]
            if(last['Activity']==pclass):
                last['EndTime']=end
                continue
        events.append({'Activity':pclass, 'StartTime':start, 'EndTime':end});
    return pd.DataFrame(events)

In [ ]:
def convertAndMergeToEvent(set_window,predictedclasses):
    events=[]
    ptree={}
    for i in range(0,len(set_window)):
        start=set_window[i]['start'];
        end=set_window[i]['end'];
        pclass=predictedclasses[i]

        if not(pclass in ptree):
            ptree[pclass]=IntervalTree()
        ptree[pclass][start:end]={'Activity':pclass, 'StartTime':start, 'EndTime':end}

    tree=IntervalTree()
    def datamerger(x,y):
        start=min(x['StartTime'],y['StartTime'])
        end=max(x['EndTime'],y['EndTime'])
        return {'Activity':x['Activity'], 'StartTime':start, 'EndTime':end}
        
    for a in ptree:
        ptree[a].merge_overlaps(data_reducer=datamerger)
        tree|=ptree[a]
    
    tree.split_overlaps()
    def data_reducer(x,y):
        res=x
        if(x['EndTime']>y['EndTime']):
            res=y
        return res
    
    tree.merge_equals(data_reducer=data_reducer)
    for inv in tree:
        events.append({'Activity':inv.data['Activity'], 'StartTime':inv.begin, 'EndTime':inv.end});
    
    events= pd.DataFrame(events)
    events=events.sort_values(['StartTime'])
    events=events.reset_index()
    events=events.drop(['index'],axis=1)
    return events

# sw,label=fullevals.iloc[0]['model']['func'].Test.set_window,fullevals.iloc[0]['testlabel']
# pev=convertAndMergeToEvent(sw,label)

# sw=np.array(sw)

# print([p['start'] for p in sw[label==7]])
# pev.loc[pev.Activity==7]

In [ ]:
# plotAct(fullevals.iloc[0]['a_events'])
# plotAct(fullevals.iloc[0]['pa_events'])

#Evaluation

In [ ]:
class AbstractEvaluation(MyTask):
    def evaluate_dataset(self,dataset,plabel,pprob):
        pass
    def confusion_matrix_dataset(self, dataset,plabel,pprob):
        pass
    def evaluate(self, rset, rlabel,plabel,pprob):
        pass
    def confusion_matrix(self, rset, rlabel,plabel,pprob):
        pass
    def eval_cm(self,cm,average=None):
        pass

##MyEvaluator

In [ ]:
class MyEvaluator(AbstractEvaluation):
    def evaluate_dataset(self,dataset,plabel,pprob):
        pa_events = convertAndMergeToEvent(dataset.set_window,plabel)
        a_events = convertAndMergeToEvent(dataset.set_window,dataset.label)
        return self.qualitymeasurement(pa_events,a_events)
    def confusion_matrix_dataset(self, dataset,plabel,pprob):
        pa_events = convertAndMergeToEvent(dataset.set_window,plabel)
        a_events =dataset.a_events # convertAndMergeToEvent(dataset.set_window,dataset.label)
        print(a_events)
        cm=myaccuracy(pa_events,a_events)
        return cm
    def evaluate(self,time_window, rlabel,plabel,pprob):
        pa_events = convertAndMergeToEvent(time_window,plabel)
        a_events = convertAndMergeToEvent(time_window,rlabel)
        return self.qualitymeasurement(pa_events,dataset.a_events)
        

    def confusion_matrix(self, time_window, rlabel,plabel,pprob):
         pa_events = convertAndMergeToEvent(dataset,plabel)
         a_events = convertAndMergeToEvent(time_window,rlabel)
         cm=myaccuracy(pa_events,a_events)
         return cm
        

    def qualitymeasurement(self,p_events,r_events):
        cm=myaccuracy(p_events,r_events)
        s=np.array(cm).sum().sum()
        correct=0    
        for i in range(0,len(cm)):
            correct+=cm[i,i]        
        return correct/s    

##Classical Evaluator

In [ ]:
class ClassicalEvaluator(AbstractEvaluation):
    # def evaluate_dataset(self,dataset,plabel,pprob):
    #     return self.evaluate(dataset.set,dataset.label,plabel,pprob,dataset.acts)
    # def confusion_matrix_dataset(self, dataset,plabel,pprob):
    #     return self.confusion_matrix(dataset.set,dataset.label,plabel,pprob,dataset.acts)
        
    # def evaluate(self, rset, rlabel,plabel,pprob,labels):
    #     ;
    
    # def confusion_matrix(self, rset, rlabel,plabel,pprob,labels):
    #     cm=confusion_matrix(rlabel,plabel,labels)
    #     return cm   

    def get_tp_fp_fn_tn(self,cm):
        cm=np.array(cm)
        np.seterr(divide='ignore', invalid='ignore')
        TP = np.diag(cm)
        FP = np.sum(cm, axis=0) - TP
        FN = np.sum(cm, axis=1).T - TP
        num_classes = len(cm)
        TN = []
        for i in range(num_classes):
            temp = np.delete(cm, i, 0)    # delete ith row
            temp = np.delete(temp, i, 1)  # delete ith column
            TN.append(temp.sum())
        return TP,FP,FN,TN
    def eval_cm(self,cm,average=None):
        pass

    # def event_cofusion_matrix(self, p_activity,r_activity):
    #     ;


###AccuracyEvaluator




In [ ]:
class Accuracy(ClassicalEvaluator):
    def evaluate(self, rset, rlabel,plabel,pprob,labels):
        return sklearn.metrics.accuracy_score(rlabel,plabel)
    
    def eval_cm(self,cm,average=None):
        TP,FP,FN,TN = self.get_tp_fp_fn_tn(cm)
        a = TP.sum()/cm.sum()
        if(average is None):
            return None
        return a

###Precision

In [ ]:
class Precision(ClassicalEvaluator):
    
    def evaluate(self, rset, rlabel,plabel,pprob,labels):
        p,r,f,s=sklearn.metrics.precision_recall_fscore_support(rlabel,plabel,1,labels ,average='macro')
        return p
    def eval_cm(self,cm,average=None):
        TP,FP,FN,TN = self.get_tp_fp_fn_tn(cm)
        p = TP/(TP+FP)
        if(average is None):
            return p
        return np.average(p[~np.isnan(p)])
    

###Recall

In [ ]:
class Recall(ClassicalEvaluator):
    def evaluate(self, rset, rlabel,plabel,pprob,labels):
        p,r,f,s=sklearn.metrics.precision_recall_fscore_support(rlabel,plabel,1,labels ,average='macro')
        return r
    def eval_cm(self,cm,average=None):
        TP,FP,FN,TN = self.get_tp_fp_fn_tn(cm)    
        r = TP/(TP+FN)
        if(average is None):
            return r
        return np.average(r[~np.isnan(r)])

###F1

In [ ]:
class F1Evaluator(ClassicalEvaluator):
     def evaluate(self, rset, rlabel,plabel,pprob,labels):
        p,r,f,s=sklearn.metrics.precision_recall_fscore_support(rlabel,plabel,1,labels ,average='macro')
        return f

     def eval_cm(self,cm,average=None):
        TP,FP,FN,TN = self.get_tp_fp_fn_tn(np.array(cm))
        #print(np.array(TP).shape,np.array(FP).shape,np.array(FN).shape,np.array(TN).shape)
        #print(TP,FP,FN,TN)
        p = TP/(TP+FP)
        r = TP/(TP+FN)
        f=2*r*p/(r+p)
        if(average is None):
            return f
        return np.average(f[~np.isnan(f)])

# Pipeline

0. load data
    1. fetch
    2. convert
    3. make train and test set
1. preprocessing
2. groupize activities
3. segment optimizer
    1. segmentByParameters
    2. featureExtractior
    3. activityExtractor # for label
    4. make model
    5. fit model
    6. evaluate





## prepare_segment

In [ ]:
def prepare_segment(dtype,func):
    segmentor=func.segmentor
    procdata=Data(segmentor.__class__.__name__)
    procdata.generator=segment(dtype.s_events,segmentor)
    procdata.set=[]
    procdata.label=[]
    procdata.set_window=[]
    procdata.acts=func.acts
    procdata.s_events=dtype.s_events
    procdata.a_events=dtype.a_events
    # it=IntervalTree()
    i=0
    for x in procdata.generator:
        if i % 10000 ==0:
            print (segmentor.shortname,i)
        i+=1
        #if(it[x['start']:x['end']]):
         #   continue;
        # if(x['start']==x['end']):
        #     it[x['start']]=1
        # else:
        #     it[x['start']:x['end']]=1
        procdata.set_window.append(x)
        #procdata.set.append(featureExtractor(x['window']))
        procdata.label.append(func.activityFeatcher.getActivity(dtype,x['window']))
        
    
    procdata.label=np.array(procdata.label)

    return procdata



## learn

In [ ]:
@profile
def learn(func,Train,acts):
    ptrain=prepare_segment(Train,func)
    ptrain.set=featureExtraction(ptrain.set_window,func.featureExtractor,True)
    func.classifier.createmodel(len(ptrain.set[0]),len(acts))
    func.classifier.train(ptrain.set, ptrain.label)
    
    if no_memory_limit:
        func.Train=ptrain
    

## eval

In [ ]:
@profile
def eval(func,Test,acts):
    ptest = prepare_segment(Test,func)
    ptest.set = featureExtraction(ptest.set_window,func.featureExtractor,False)
    #func.classifier.evaluate(ptest.set, ptest.label)
    #func.Test=ptest
    if no_memory_limit:
        func.Test=ptest
    else:
        func.Test=Data('Test')
        
    predicted=func.classifier.predict(ptest.set)
    predictedclasses=func.classifier.predict_classes(ptest.set)    
    
    func.Test.predict=predicted
    func.Test.predict_classes=predictedclasses
    cm=confusion_matrix(ptest.label,predictedclasses,func.acts)
    pa_events=convertAndMergeToEvent(ptest.set_window,predictedclasses)
    #ra_events=convertAndMergeToEvent(model['func'].Test.set_window,testlabel)
    #ra_events=model['Test'].a_events
    cm2=event_confusion_matrix(ptest.a_events,pa_events,func.acts)
    func.Test.a_events=ptest.a_events
    func.Test.pa_events=pa_events
    func.Test.label=ptest.label
    func.Test.cm=cm
    func.Test.mycm=cm2
    q=func.evaluator.eval_cm(cm,'micro')
    print('===============',func.classifier.shortname,' Quality:',q)
    return q


## learn_eval

In [ ]:
def learn_eval(shortname,func,TTrain,TTest,acts):   
    learn(func,TTrain,acts)
    quality = eval(func,TTest,acts)
    return quality

## JustifiySet

In [ ]:
def justifySet(acts,Train,Test):
    inp=[Train,Test]
    out=[]
    if(acts[0]!=0):
        acts.insert(0,0)
        
    act_map= {a:i for i,a in enumerate(acts) }
    for dtype in inp:
        ndtype=Data(dtype.name)
        ndtype.s_events=dtype.s_events
        ndtype.a_events=dtype.a_events.copy()
        ndtype.a_events.Activity=dtype.a_events.Activity.apply(lambda x:act_map[x] if x in act_map else 0)
        ndtype.a_events_tree=IntervalTree()
        for i,act in ndtype.a_events.iterrows():
            ndtype.a_events_tree[act.StartTime.value:act.EndTime.value]=act  
        out.append(ndtype)
    return out[0],out[1]#Train,Test

In [ ]:
def convertArray2ParamsDic(array,params):
    paramDic={}
    for i,p in enumerate(params):
            paramDic[p['var']]=array[i]
    return paramDic

## Define Segmenations Methods

In [ ]:
available_segmentations=[
#                         # #{'method': Probabilistic(), 'params':[],'findopt':False},
#                         {'method': lambda:FixedSlidingWindow(), 'params':[
#                                     {'var':'size','min':pd.Timedelta(10, unit='s').total_seconds(), 'max': pd.Timedelta(10, unit='m').total_seconds(), 'type':'float','init':pd.Timedelta(30, unit='s').total_seconds()},
#                                     {'var':'shift','min':pd.Timedelta(10, unit='s').total_seconds(), 'max': pd.Timedelta(10, unit='m').total_seconds(), 'type':'float','init':pd.Timedelta(1, unit='s').total_seconds()}
#                                 ],
#                          'findopt':True},
                         {'method': lambda:FixedEventWindow(), 'params':[
                                    {'var':'size','min':10, 'max': 30, 'type':'int','init':20},
                                    {'var':'shift','min':1, 'max': 20, 'type':'int','init':1}
                                ],
                         'findopt':False},
                         {'method': lambda:FixedSlidingWindow(), 'params':[
                                     {'var':'size','min':pd.Timedelta(1, unit='s').total_seconds(), 'max': pd.Timedelta(30, unit='m').total_seconds(), 'type':'float','init':pd.Timedelta(15, unit='s').total_seconds()},
                                     {'var':'shift','min':pd.Timedelta(1, unit='s').total_seconds(), 'max': pd.Timedelta(30, unit='m').total_seconds(), 'type':'float','init':pd.Timedelta(1, unit='s').total_seconds()}
                                 ],
                         'findopt':False},
                        #  {'method': lambda:FixedTimeWindow(), 'params':[
                        #              {'var':'size','min':pd.Timedelta(1, unit='s').total_seconds(), 'max': pd.Timedelta(30, unit='m').total_seconds(), 'type':'float','init':pd.Timedelta(15, unit='s').total_seconds()},
                        #              {'var':'shift','min':pd.Timedelta(1, unit='s').total_seconds(), 'max': pd.Timedelta(30, unit='m').total_seconds(), 'type':'float','init':pd.Timedelta(1, unit='s').total_seconds()}
                        #          ],
                        #  'findopt':False},
                         {'method': lambda:Probabilistic(), 'params':[
                                 ],
                         'findopt':False}
                        ]

##Define FeatureExtractionMethods

In [ ]:
available_featureExtraction=[
                        # {'method': lambda:SimpleFeatureExtraction(), 'params':[
                        #         ],
                        #  'findopt':False},
                        #  {'method': lambda:DeepLearningFeatureExtraction(), 'params':[
                        #             {'var':'size','min':10, 'max': 20, 'type':tf.int8,'init':50},
                        #             {'var':'layers','min':1, 'max': 3, 'type':tf.int8,'init':pd.Timedelta(20, unit='s').total_seconds()}
                        #         ],
                        #  'findopt':False},
                        {'method': lambda:Cook1FeatureExtraction(), 'params':[
                                ],
                         'findopt':False},
                        ]

## Define Classifiers

In [ ]:
available_classifiers=[
                        #     {'method': lambda:SVMClassifier(), 'params':[
                                
                        #         ],
                        #  'findopt':False},
                        {'method': lambda:LSTMTest(), 'params':[
                                {'var':'epochs','min':10, 'max': 20, 'type':tf.int8,'init':3},
                                ],
                         'findopt':False},
                        ]

##ParameterMaker

In [ ]:
class ParamMaker:
    def __init__(self,items):
        self.items=items

    def convertToArray(self):
        #seg.params.length
        x0=[]
        bounds=[]

        for item in self.items:
            print(item)
            if(item['findopt']):
                for p in item['params']:
                    bounds.append([p['min'],p['max']])
                    x0.append(p['init'])
        return x0,bounds

    def getParams(self,X,i):
        items=self.items
        x0=[];
        
        if not items[i]['findopt']:
            for p in items[i]['params']:
                x0.append(p['init'])
            return convertArray2ParamsDic(x0,items[i]['params'])
        fi=0
        for j in range(i):
            if(items[j]['findopt']):
                fi=fi+len(items[j]['params'])
            
        return convertArray2ParamsDic(X[fi:fi+len(items[i]['params'])],items[i]['params'])
        



## Optimizer

In [ ]:
from memory_profiler import profile

class OptLearn:
    def __init__(self,shortname,result,func,TTrain,TTest,acts):
        self.shortname=shortname
        self.result=result
        self.func=func
        self.TTrain=TTrain
        self.TTest=TTest
        self.acts=acts
    
    @profile
    def run(self):
        shortname=self.shortname
        result=self.result
        func=self.func
        TTrain=self.TTrain
        TTest=self.TTest
        acts=self.acts
        
        print(shortname,'start')
        
        
        func.segmentor.reset()
        func.featureExtractor.reset()
        params=ParamMaker([func.segmentor.method,func.featureExtractor.method,func.classifier.method])
        x0,bounds=params.convertToArray()

        result['history']={}
        
        def qfunc(param): 
            segparams=params.getParams(param,0)
            feaparams=params.getParams(param,1)
            claparams=params.getParams(param,2)
            if not func.featureExtractor.applyParams(feaparams):
                return -100000
            if not func.segmentor.applyParams(segparams):
                return -100000
            if not func.classifier.applyParams(claparams):
                return -100000
            print(func.segmentor.params)
            print(shortname,'segparam:',segparams,'feaparam:',feaparams,'claparm:',claparams)
            q=learn_eval(shortname,func,TTrain,TTest,acts)
            if no_memory_limit:
                result['last']=result['history'][str(param)]={'q':q, 'TTest':TTest, 'TTrain':TTrain}
            
            return -q
        
        if len(x0)>0:
            optq=skopt.forest_minimize(qfunc,bounds)
        else:
            optq={'x':x0, 'q':qfunc(x0)};
        print(shortname,optq)
        
        result['optq']=optq
        result['segparams']=params.getParams(optq['x'],0)
        result['feaparams']=params.getParams(optq['x'],1)
        result['claparams']=params.getParams(optq['x'],2)

        #result['Test'] =func.Test
        #pa_events=convertAndMergeToEvent(func.Test.set_window,func.Test.label)
        pa_events=func.Test.pa_events
        result['Test']={'pa_events':pa_events,
                        'a_events':func.Test.a_events,
                        #'label':func.Test.label,
                        #'predict': func.Test.predict,
                        #'predict_classes':func.Test.predict_classes,
                        'cm':func.Test.cm,#confusion_matrix(func.Test.label,func.Test.predict_classes,func.acts),
                        'mycm':func.Test.mycm#event_confusion_matrix(func.Test.a_events,pa_events,func.acts)
                        }

        if not(no_memory_limit):
            id_func=id(func)
            del id_func
            
            id_func=id(self.func.Test)
            del id_func
            id_func=id(self.func)
            del id_func
            id_func=id(self.TTrain)
            del id_func
            id_func=id(self.TTest)
            del id_func


        self.result=result
        return result


##Load Dataset


In [ ]:
# 0
## 0.1, 0.2
loadA4HDataSet()
#loadHome1Dataset()

## Pre-Run


In [ ]:
no_memory_limit=False
def prepare_run():
    #3 
    # gacts=[[a] for a in activities_map]
    # gacts.append([a for a in activities_map])
    gacts=[[a for a in activities_map]]
    fullmodel={}
    fold=5
    ## 0.3
    #ttmaker=makeTrainTest(sensor_events,activity_events)
    ttmaker=makeFoldTrainTest(sensor_events,activity_events,fold)
    allpool=[];
    for f,(Train0,Test0) in enumerate(ttmaker):
        print('=========Fold ',f,' ===========')
        model=fullmodel[f]={}
        #1
        Train=preprocessing(Train0)
        Test=preprocessing(Test0)

        for dtype in [Train,Test]:
            dtype.proc={}
            dtype.generator={}
            dtype.set={}
            dtype.label={}
            dtype.set_window={}

        for indx,acts in enumerate(gacts):
            TTrain,TTest=justifySet(acts,Train,Test)
            
            model=fullmodel[f][indx]={}
            model['acts']=acts
            model['acts_name']=activities[acts]
            model['TTrain']=TTrain
            model['TTest']=TTest

            for segmethod in available_segmentations:
                segmentor=segmethod['method']()
                segmnetor_name=segmentor.__class__.__name__
                model=fullmodel[f][indx][segmnetor_name]={}
                model['segmentor']=segmentor

                segmentor.precompute(TTrain.s_events,TTrain.a_events,acts)
                for feamethod in available_featureExtraction:
                    featureExtractor=feamethod['method']()
                    featureExtractor_name=featureExtractor.__class__.__name__
                    for classimethod in available_classifiers:
                        classifier=classimethod['method']()
                        classifier_name=classifier.__class__.__name__

                        #
                        filterkey=segmnetor_name+'-'+featureExtractor_name+"-"+classifier_name
                        shortname='F'+str(f)+'-'+str(indx)+'-'+filterkey
                        
                        result=fullmodel[shortname]={}
                        result['fold']=f;
                        result['indx']=indx;
                        if no_memory_limit:
                            result['segmentor']=segmentor;
                            result['featureExtractor']=featureExtractor;
                            result['classifier']=classifier
                        result['segmentorName']=segmnetor_name;
                        result['featureExtractorName']=featureExtractor_name;
                        result['classifierName']=classifier_name
                        if no_memory_limit:
                            result['TTrain']=TTrain
                            result['TTest']=TTest
                        result['acts']=acts
                        result['acts_name']=activities[acts]
                        result['shortname']=shortname
                        result['filterkey']=filterkey
                        segmentor.method=segmethod
                        featureExtractor.method=feamethod
                        classifier.method=classimethod
                        
                        func=Data('Functions');
                        func.segmentor=segmentor
                        func.featureExtractor=featureExtractor
                        func.classifier=classifier
                        func.activityFeatcher=CookActivityFeatcher()
                        #func.activityFeatcher=OldActivityFeatcher()
                        #func.evaluator=MyEvaluator()
                        func.evaluator=Accuracy()
                        func.acts=acts
                        for k in func.__dict__:
                            obj=func.__dict__[k]
                            if isinstance(obj,MyTask):                               
                                obj.shortname=shortname;
                                obj.func=func;

                        if no_memory_limit:    
                            result['func']=func;

                        optl=OptLearn(shortname,result,func,TTrain,TTest,acts)
                        allpool.append(optl)
                        return allpool;
    return allpool

def runOptLearn(optl,test=0):
    try:
        return optl.run();
    except Exception as e:
        if test:
            raise e
        import sys
        import traceback
        print(e, file=sys.stderr)
        traceback.print_exc()
        return optl

def run(allpool, test):
    #return [runOptLearn(allpool[0])]
    if test:
        result= [runOptLearn(p,test) for p in allpool]
    else:
        with parallel_backend('threading'):
            result= (Parallel()(delayed(runOptLearn)(p) for p in allpool))
        
    success=[]
    fail=[]
    for i in range(len(result)):
        if(type(result[i]) is OptLearn):
            print("!!!FAILED:",i,result[i].shortname)
            fail.append(result[i])
        else:
            success.append(result[i])   
    # for pool in allpool:
    #     runOptLearn(pool)
    #     break;
    print('finish')
    return success,fail
allpool=prepare_run();


##Execute

In [ ]:
success,failed=run(allpool,True)
runs=pd.DataFrame(success)

## Save Runs Result

In [ ]:
#%store  
#success1=success
#success =1
%store success




## Load Runs Result

In [ ]:
%store -r
runs=pd.DataFrame(success)

## PrepareEval

In [ ]:
def prepareEval(runs):
    #myeval=MyEvaluator()
    #defeval=Accuracy()

    fullevals=[]
    filterkeys=runs.filterkey.unique()
    for filterkey in filterkeys:
        print("-----------"+filterkey+"--------")
        runsdata=runs.loc[runs.filterkey==filterkey];
        sumcm=np.matrix([0])
        sumcm2=np.matrix([0])
        
        for f in runsdata.fold:
            model=runsdata.loc[runsdata.fold==f].iloc[0]
            #testset=model['Test'].set
            #testlabel=model['Test'].label
            #plabel=model['Test'].predict_classes
            #pprob=model['Test'].predict

            #cm=confusion_matrix(testlabel,plabel,model['acts'])
            #pa_events=convertAndMergeToEvent(model['Test'].set_window,plabel)
            #ra_events=convertAndMergeToEvent(model['func'].Test.set_window,testlabel)
            #ra_events=model['Test'].a_events
            #cm2=event_confusion_matrix(ra_events,pa_events,model['acts'])
            # cm2=event_confusion_matrix(model['func'].Test.a_events,ra_events,model['acts'])
            #cm2=event_confusion_matrix(ra_events,ra_events,model['acts'])
            #cm2=myeval.confusion_matrix_dataset(model['func'].Test,plabel,pprob)
            cm=model['Test']['cm']
            cm2=model['Test']['mycm']
            pa_events=model['Test']['pa_events']
            a_events=model['Test']['a_events']
            sumcm=sumcm+cm
            sumcm2=sumcm2+cm2
            acts=model['acts_name']
            evmod={}    
            evmod['shortname']=model['shortname']
            evmod['fold']=f
            evmod['filterkey']=filterkey
            evmod['cm']=cm
            evmod['mycm']=cm2
            #evmod['testset']=testset
            #evmod['testlabel']=testlabel
            #evmod['plabel']=plabel
            #evmod['pprob']=pprob
            evmod['a_events']=a_events
            evmod['pa_events']=pa_events
            evmod['acts']=acts
            evmod['model']=model
            fullevals.append(evmod)
        evmod={}
        evmod['shortname']='total-'+filterkey
        evmod['fold']=-1
        evmod['filterkey']=filterkey
        evmod['cm']=sumcm
        evmod['mycm']=sumcm2
        #evmod['testset']=None
        #evmod['testlabel']=None
        #evmod['plabel']=None
        #evmod['pprob']=None
        evmod['a_events']=None
        evmod['pa_events']=None
        evmod['acts']=acts
        evmod['model']=None
        fullevals.append(evmod)

    return fullevals;
fullevals=prepareEval(runs)
fullevals=pd.DataFrame(fullevals)

##Evals

In [ ]:
evals=[]
evals.append(Accuracy())
evals.append(F1Evaluator())
evals.append(Precision())
evals.append(Recall())


filterkeys=fullevals.filterkey.unique()
evdata=fullevals#.loc[fullevals.fold==-1]
full_eval_res=[];
for i,data in evdata.iterrows():
    eval_res={}
    myeval_res={}
    for ev in evals:
        name=ev.__class__.__name__
        cm=data['cm']#[1:,1:]
        mycm=data['mycm']#[1:,1:]
        e2=ev.eval_cm(cm,average='micro')
        eval_res[name]=round(e2,2)
        e3=ev.eval_cm(mycm,average='micro')
        myeval_res[name]=round(e3,2)
        eval_res['type']='Normal'
        myeval_res['type']='My'
        myeval_res['filterkey']=data['filterkey']
        eval_res['filterkey']=data['filterkey']
        myeval_res['fold']=data['fold']
        eval_res['fold']=data['fold']
        

        
    full_eval_res.append(eval_res)    
    full_eval_res.append(myeval_res)    
    print(data['shortname'],'No',eval_res)
    print(data['shortname'],'MY',myeval_res)
        
    #plot_confusion_matrix(sumcm,acts,figsize=[15,7])


In [ ]:
tbl=pd.DataFrame(full_eval_res)
pd.pivot_table(tbl,index=['filterkey'],values=['Accuracy','F1Evaluator','Precision','Recall'],columns='type')
#tbl

## Draw CM

In [ ]:
evals=[]
evals.append(Accuracy())
evals.append(F1Evaluator())
evals.append(Precision())
evals.append(Recall())

filterkeys=fullevals.filterkey.unique()
evdata=fullevals.loc[fullevals.fold==-1]
for i,data in evdata.iterrows():
    #for ev in evals:
    ev=F1Evaluator()
    name=ev.__class__.__name__
    cm=data['cm']
    mycm=data['mycm']
    acts=data['acts']
    e2=ev.eval_cm(cm,average=None)
    
    print(data['shortname'],'No')
     
    plot_confusion_matrix(cm,acts,figsize=[25,12])    
    print(data['shortname'],'MY')
    plot_confusion_matrix(mycm,acts,figsize=[25,12])


##Plot F Score per activity

In [ ]:
import matplotlib.pyplot as plt
def get_new_fig(fn, figsize=[15,9]):
    """ Init graphics """
    fig1 = plt.figure(fn, figsize)
    ax1 = fig1.gca()   #Get Current Axis
    ax1.cla() # clear existing plot
    return fig1, ax1

evdata=fullevals.loc[fullevals.fold==-1]
bar_count=len(evdata)
x = np.arange(len(activities))  # the label locations

fig, ax = get_new_fig(',',[20,5])#plt.subplots()
rects=[]
width=.7/(bar_count*2)
for i,(k,data) in enumerate(evdata.iterrows()):
    #for ev in evals:
    ev=F1Evaluator()
    name=ev.__class__.__name__
    e2=(100*ev.eval_cm(data['cm'],average=None)).round()
    splt=data['filterkey'].split('-');
    rects.append(ax.bar(x - 1.2*width*(i+.5), e2, width, label=splt[0]))
    
    e3=(100*ev.eval_cm(data['mycm'],average=None)).round()
    
    rects.append(ax.bar(x + (1.2*width*(i+.5)), e3, width, label='MY'+splt[0]))

# Add some text for labels, title and custom x-axis tick labels, etc.
ax.set_ylabel(name)
ax.set_title(name+'')
ax.set_xticks(x)
ax.set_xticklabels(activities_map_inverse,rotation=-90)

ax.legend()

def autolabel(rects):
    """Attach a text label above each bar in *rects*, displaying its height."""
    for rect in rects:
        height = rect.get_height()
        ax.annotate('{}'.format(height),
                    xy=(rect.get_x() + rect.get_width() / 2, height),
                    xytext=(0, 3),  # 3 points vertical offset
                    textcoords="offset points",
                    ha='center', va='bottom')

#for rect in rects:
    #autolabel(rect)

fig.tight_layout()
fig.patch.set_facecolor('white')
plt.show()

#ALI

In [ ]:
data=fullevals.loc[fullevals.fold==0].iloc[0]
data['cm']=data['cm'][0]
tp,fp,fn,tn=F1Evaluator().get_tp_fp_fn_tn(data['cm'])
print(tp)
print(fp)
print(fn)
print(tn)
#print(activities_map)
#print(evdata['cm'])
#plot_confusion_matrix(evdata['cm'],activities,[15,8])
dur=activity_events.loc[activity_events.Activity==1].Duration.values

#print(dur)

model=fullevals.iloc[0]['model']
seg=model['segmentor']
aes=data['model'].TTest.a_events#.loc[activity_events.Activity==6]
count=0
for k,ae  in aes.iterrows():
    count += len(data['model'].TTest.s_events.loc[(data['model'].TTest.s_events.time>=ae.StartTime) & (data['model'].TTest.s_events.time<=ae.EndTime)])

print(count)
print(data['cm'])
data['model'].func.segmentor.reset()
newTest=prepare_segment(data['model'].TTest,data['model'].func)
#len(data['model'].func.Test.set)


In [ ]:
len(newTest.label)
len(data['model'].TTest.s_events)

##Accuracy

In [ ]:
# pa_events=model[0]['Probabilistic']['[]']['pa_events']
#pa_events=model[0]['FixedSlidingWindow']['DeepLearningFeatureExtraction']['[30.0, 20.0, 50, 20.0]']['pa_events']

#oldruns=runs
#runs=success

evals=[]
myeval=MyEvaluator()
defeval=Accuracy()
evals.append(Accuracy())
#evals.append(MyEvaluator())
evals.append(F1Evaluator())
evals.append(Precision())
evals.append(Recall())
fullevals=[]
filterkeys=runs.filterkey.unique()
for filterkey in filterkeys:
    print("-----------"+filterkey+"--------")
    runsdata=runs.loc[runs.filterkey==filterkey];
    cm={}
    cm2={}
    sumcm=np.matrix([0])
    sumcm2=np.matrix([0])
    
    for f in runsdata.fold:
        model=runsdata.loc[runsdata.fold==f].iloc[0]
        testset=model['func'].Test.set
        testlabel=model['func'].Test.label
        plabel=model['func'].classifier.predict_classes(testset)
        pprob=model['func'].classifier.predict(testset)

        cm[f]=defeval.confusion_matrix_dataset(model['func'].Test,plabel,pprob)
        cm2[f]=myeval.confusion_matrix_dataset(model['func'].Test,plabel,pprob)
        sumcm=sumcm+cm[f]
        sumcm2=sumcm2+cm2[f]
        eval_res={}
        eval_res_dtl={}
        myeval_res={}
        myeval_res_dtl={}
        for ev in evals:
            #e1=ev.evaluate_dataset(model['func'].Test,plabel,pprob)
            name=ev.__class__.__name__
            e2=ev.eval_cm(cm[f],average='micro')
            eval_res[name]=round(e2,2)
            e3=ev.eval_cm(cm2[f],average='micro')
            myeval_res[name]=round(e3,2)
            e22=ev.eval_cm(cm[f],average=None)
            eval_res_dtl[name]=e22
            e32=ev.eval_cm(cm2[f],average=None)
            myeval_res_dtl[name]=e32

        acts=model['acts_name']#[1:]
        print(model['shortname'],'No',eval_res)
        print(model['shortname'],'MY',myeval_res)
        evmod={}    
        evmod['shortname']=model['shortname']
        evmod['fold']=f
        evmod['filterkey']=filterkey
        evmod['normal_eval']=eval_res
        evmod['my_eval']=myeval_res
        evmod['normal_eval_dtl']=eval_res_dtl
        evmod['my_eval_dtl']=myeval_res_dtl
        evmod['cm']=cm
        evmod['mycm']=cm2
        evmod['testset']=testset
        evmod['testlabel']=testlabel
        evmod['plabel']=plabel
        evmod['pprob']=pprob
        evmod['acts']=acts
        evmod['model']=model
        fullevals.append(evmod)
    #sumcm=sumcm[1:,1:]
    eval_res={}
    myeval_res={}
    for ev in evals:
        e2=ev.eval_cm(sumcm)
        name=ev.__class__.__name__
        eval_res[name]=round(e2,2)
        e3=ev.eval_cm(sumcm2)
        myeval_res[name]=round(e3,2)
    print('total',filterkey,'No',eval_res)
    print('total',filterkey,'MY',myeval_res)
    evmod={}
    evmod['shortname']='total-'+filterkey
    evmod['fold']=-1
    evmod['filterkey']=filterkey
    evmod['normal_eval']=eval_res
    evmod['my_eval']=myeval_res
    evmod['cm']=sumcm
    evmod['mycm']=sumcm2
    evmod['testset']=None
    evmod['testlabel']=None
    evmod['plabel']=None
    evmod['pprob']=None
    evmod['acts']=acts
    evmod['model']=None
    fullevals.append(evmod)
    #plot_confusion_matrix(sumcm,acts,figsize=[15,7])


In [ ]:
evalresult=pd.DataFrame(fullevals)
a=evalresult.fold.values
a.tolist()

In [ ]:
import matplotlib.pyplot as plt
def get_new_fig(fn, figsize=[9,9]):
    """ Init graphics """
    fig1 = plt.figure(fn, figsize)
    ax1 = fig1.gca()   #Get Current Axis
    ax1.cla() # clear existing plot
    return fig1, ax1

labels = ['G1', 'G2', 'G3', 'G4', 'G5']
men_means = [20, 34, 30, 35, 27]
women_means = [25, 32, 34, 20, 25]

x = np.arange(len(labels))  # the label locations
width = 0.35  # the width of the bars

fig, ax = get_new_fig(',',[15,5])#plt.subplots()
rects1 = ax.bar(x - width/2, men_means, width, label='Men')
rects2 = ax.bar(x + width/2, women_means, width, label='Women')
rects3 = ax.bar(evalresult.fold, evalresult.fold, width,label='Fold')
rects4 = ax.bar(evalresult.fold, evalresult.fold, width,label='Fold1')
# Add some text for labels, title and custom x-axis tick labels, etc.
ax.set_ylabel('Scores')
ax.set_title('Scores by group and gender')
ax.set_xticks(x)
ax.set_xticklabels(labels)
ax.legend()


def autolabel(rects):
    """Attach a text label above each bar in *rects*, displaying its height."""
    for rect in rects:
        height = rect.get_height()
        ax.annotate('{}'.format(height),
                    xy=(rect.get_x() + rect.get_width() / 2, height),
                    xytext=(0, 3),  # 3 points vertical offset
                    textcoords="offset points",
                    ha='center', va='bottom')


autolabel(rects1)
autolabel(rects2)
autolabel(rects3)
fig.tight_layout()
fig.patch.set_facecolor('white')
plt.show()




In [ ]:
model=runs.loc[runs.filterkey=='FixedEventWindow-Cook1FeatureExtraction-SVMClassifier'].iloc[0]

testset=model['func'].Test.set
testlabel=model['func'].Test.label
plabel=model['func'].classifier.predict_classes(testset)
pprob=model['func'].classifier.predict(testset)
e1=evalution.evaluate_dataset(model['func'].Test,plabel,pprob)
e2=evalution2.evaluate_dataset(model['func'].Test,plabel,pprob)
print(model['shortname'],'Cook Ev:',e1,' MyEv:',e2)
pa_events=convertAndMergeToEvent(model['func'].Test.set_window,plabel)
plotAct(pa_events)

In [ ]:
print('F0-0-FixedSlidingWindow-Cook1FeatureExtraction-SVMClassifier Cook Ev: 0.6458036984352774  MyEv: 0.9235096013309696')
plotAct(pa_events.iloc[0:3000])

In [ ]:
plotAct(activity_events)

##End